#H-1B Data Analysis



The **H-1B program** allows companies and other employers in the United States to temporarily employ foreign workers in occupations that require the theoretical and practical application of a body of highly specialized knowledge and a bachelor’s degree or higher in the specific specialty, or its equivalent. 

For international students studying in the US, securing the H-1B visa via the lottery system is highly dependent on luck. Not only is it harsh, but also a lot of highly skilled workers who could contribute to the US economy are lost. If an H-1B Visa is not received timely, internationals have no options but to head back to their home countries and hunt for jobs elsewhere.

Keeping all this in mind, I was curious to perform EDA and analyze underlying trends on H-1b data gathered over the years. Thanks to kaggle, I was able to find a comprehensive dataset harboring H-1B data spanning 6 years.

In [13]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
import random

## The Dataset

The dataset employed in this notebook is taken from [kaggle](https://www.kaggle.com/rakeshchintha/oflc-h1b-data). All in all, the size of the data is ~500 MB. However, due to size and computational constraints in google colab, I condensed the size to a mere 2.5 MB. 

*Note*: The dataset size was reduced using [this](https://stackoverflow.com/questions/22258491/read-a-small-random-sample-from-a-big-csv-file-into-a-python-data-frame) as a reference. Only 10% of the data was retained. However, the general trends, as you shall see in the visualizations below, represent that of the original data. For each year, almost an equal amount of rows were sampled.

In [15]:
h1b_df = pd.read_csv('https://github.com/snehilchopra/H-1B_BDI475/raw/main/out.csv', error_bad_lines=False, encoding='latin-1')

## Preview of the Data


In [3]:

h1b_df.shape
h1b_df.info()
h1b_df.head(5)
h1b_df.sample(5)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 300443 entries, 0 to 300442
Data columns (total 12 columns):
 #   Column              Non-Null Count   Dtype  
---  ------              --------------   -----  
 0   Unnamed: 0          300443 non-null  int64  
 1   CASE_STATUS         300441 non-null  object 
 2   EMPLOYER_NAME       300435 non-null  object 
 3   SOC_NAME            298613 non-null  object 
 4   JOB_TITLE           300437 non-null  object 
 5   FULL_TIME_POSITION  300440 non-null  object 
 6   PREVAILING_WAGE     300435 non-null  float64
 7   YEAR                300441 non-null  float64
 8   lon                 289589 non-null  float64
 9   lat                 289589 non-null  float64
 10  City                300428 non-null  object 
 11  State               300443 non-null  object 
dtypes: float64(4), int64(1), object(7)
memory usage: 27.5+ MB


Unnamed: 0 CASE_STATUS  ...           City            State
153149     1529991   CERTIFIED  ...    WESTMINSTER         COLORADO
112882     1129209   CERTIFIED  ...      CHARLOTTE   NORTH CAROLINA
56801       568440   CERTIFIED  ...        CHICAGO         ILLINOIS
86979       868171   CERTIFIED  ...       PORTLAND            MAINE
143872     1437919   CERTIFIED  ...  SANTA CLARITA       CALIFORNIA

[5 rows x 12 columns]

## H-1B Petitions per year

People felt quite safe and confident to work in the US during the Obama administration, which meant an increase in the number of petitions filed during his tenure.

Let's verify this ourselves.


In [16]:
df_h1b_cases_by_date = h1b_df.groupby(['YEAR']).size().reset_index(name='Number of petitions')

fig_bar = px.bar(df_h1b_cases_by_date, x='YEAR', y='Number of petitions', title='Number of H-1B petitions by year', width=700, height=800)
fig_line = px.line(df_h1b_cases_by_date, x='YEAR', y='Number of petitions', title='Number of H-1B petitions by year')

fig_bar.show()
fig_line.show()


As you can see, there was a stark increase in the number of cases filed from 2011-2016. 

## Number of Cases filed per State

Now let's examine the number of petitions filed per state.

In [5]:
df_h1b_cases_by_state = h1b_df.groupby(['State']).size().reset_index(name='Number of petitions')

fig = px.bar(
    df_h1b_cases_by_state,
    x='Number of petitions',
    y='State',
    title='H-1B Breakdown by State',
    height=2500,
    orientation='h'
)

fig.update_yaxes(categoryorder='total ascending')

fig.show()

As you can see, CA and TX top the list, mostly because of an abundant of tech jobs. NY places third, mostly because of jobs in the finance and economic sector.

## Case Status 

The pie chart below shows that a majority of the petitions were approved by the USCIS over the course of 2011-2016.

In [6]:
fig = px.pie(
    h1b_df,
    names='CASE_STATUS',
    title='Breakdown of Case Status for the years 2011-2016',
    width=800,
    height=700
)
fig.show()

## Breakdown of Case Status State-wise

In [7]:
df_h1b_cases_by_state_case_status = h1b_df.groupby(['State', 'CASE_STATUS']).size().reset_index(name='Number of petitions')

fig = px.bar(
    df_h1b_cases_by_state_case_status,
    x='Number of petitions',
    y='State',
    color='CASE_STATUS',
    title='Breakdown of H-1B Case Status by State from 2011-2016',
    height=2000,
    orientation='h'
)

fig.update_yaxes(categoryorder='total ascending')

fig.show()

## Number of H-1B Petitions FIled Company-Wise

The treemap below gives a comprehensive visualization of the companies with the most number of H-1B petition filings. Most of the companies are either in the tech or the consulting industry.

In [9]:
df_h1b_cases_by_company = h1b_df.groupby(['EMPLOYER_NAME']).size().reset_index(name='Number of petitions').sort_values(by='Number of petitions', ascending=False)[:20]

fig = px.treemap(
    df_h1b_cases_by_company,
    path=['EMPLOYER_NAME'],
    title='Top H-1B Breakdown by company',
    values=df_h1b_cases_by_company['Number of petitions'],
    width=800,
    height=900
)

fig.show()

## Number of H-1B Petitions Per Job
The pie chart below represents those jobs with the highest number of H-1B petitions filed. As can be easily deduced, again, most of the jobs revolve in tech or consulting.

In [10]:
df_h1b_cases_by_job = h1b_df.groupby(['JOB_TITLE']).size().reset_index(name='Number of petitions').sort_values(by='Number of petitions', ascending=False)[:20]

fig = px.pie(
    df_h1b_cases_by_job,
    names='JOB_TITLE',
    title='Breakdown of H_1B petition per job for the years 2011-2016',
    values=df_h1b_cases_by_job['Number of petitions'],
    width=800,
    height=700
)
fig.show()

## Number of Accepted H-1B Petitions Company-Wise


In [12]:
df_h1b_accepted_cases_per_employer = h1b_df[h1b_df['CASE_STATUS'] == 'CERTIFIED'].groupby(['EMPLOYER_NAME']).size().reset_index(name='Number of petitions').sort_values(by='Number of petitions', ascending=False)[:20]

fig = px.bar(
    df_h1b_accepted_cases_per_employer,
    x=df_h1b_accepted_cases_per_employer['Number of petitions'],
    y='EMPLOYER_NAME',
    title='Number of Accepted H-1B Petitions by Company ',
    height=2000,
    orientation='h'
)

fig.update_yaxes(categoryorder='total ascending')
fig.show()